# Build a recommender system via collaborative filtering

In [1]:
from collections import defaultdict
from functools import partial
import json
import re
import os
import sys

import numpy as np
import pandas as pd
import plotly.express as px
import plotly.graph_objects as go
from surprise import Reader, Dataset, SVD, accuracy
from surprise.model_selection import cross_validate, train_test_split

sys.path.append("../src")
from manipulate_data import parse_date_in_title, get_value_for_key

In [2]:
def get_top_k(predictions, k=10):
    """Return the top-k recommendation for each user from a set of predictions.

    Args:
        predictions (list of Prediction objects): The list of predictions, as
            returned by the test method of an algorithm.
        k (int): The number of recommendation to output for each user. Default
            is 10.

    Returns:
    A dict where keys are user (raw) ids and values are lists of tuples:
        [(raw item id, rating estimation), ...] of size k.
    """

    # First map the predictions to each user.
    top_k = defaultdict(list)
    for uid, iid, true_r, est, _ in predictions:
        top_k[uid].append((iid, est))

    # Then sort the predictions for each user and retrieve the k highest ones.
    for uid, user_ratings in top_k.items():
        user_ratings.sort(key=lambda x: x[1], reverse=True)
        top_k[uid] = user_ratings[:k]

    return top_k


In [3]:
year_recommendations = 2002

## Load and prepare data

In [4]:
df_movies = pd.read_csv("../data/movies_small.csv")
# parse date
df_movies['date'] = df_movies['title'].apply(parse_date_in_title)
df_movies.head(5)

movieId                               title  \
0        1                    Toy Story (1995)   
1        2                      Jumanji (1995)   
2        3             Grumpier Old Men (1995)   
3        4            Waiting to Exhale (1995)   
4        5  Father of the Bride Part II (1995)   

                                        genres    date  
0  Adventure|Animation|Children|Comedy|Fantasy  1995.0  
1                   Adventure|Children|Fantasy  1995.0  
2                               Comedy|Romance  1995.0  
3                         Comedy|Drama|Romance  1995.0  
4                                       Comedy  1995.0

In [5]:
# open csv with the users and ratings, main data for the collaborative filtering
df_ratings = pd.read_csv("../data/ratings_small.csv")
df_ratings

userId  movieId  rating   timestamp
0            1        1     4.0   964982703
1            1        3     4.0   964981247
2            1        6     4.0   964982224
3            1       47     5.0   964983815
4            1       50     5.0   964982931
...        ...      ...     ...         ...
100831     610   166534     4.0  1493848402
100832     610   168248     5.0  1493850091
100833     610   168250     5.0  1494273047
100834     610   168252     5.0  1493846352
100835     610   170875     3.0  1493846415

[100836 rows x 4 columns]

In [6]:
# add date to rating data
df_ratings = df_ratings.merge(
    df_movies[['movieId', 'date']], 
    how='left', 
    on='movieId'
)

In [7]:
ratings_per_year = pd.value_counts(df_ratings.date).reset_index()
ratings_per_year.columns = ['year', 'nb_ratings']
fig = px.bar(ratings_per_year, x='year', y='nb_ratings')
fig.show()

In [8]:
# find most rated movies in 2002
df_ratings[df_ratings.date == year_recommendations]

userId  movieId  rating   timestamp    date
288          3     5048     0.5  1306464284  2002.0
952          7     5218     3.5  1106712866  2002.0
953          7     5349     3.5  1106636606  2002.0
954          7     5378     0.5  1106635735  2002.0
955          7     5445     4.0  1106636707  2002.0
...        ...      ...     ...         ...     ...
100003     610     7090     3.0  1493845971  2002.0
100037     610     7981     4.0  1493847542  2002.0
100098     610    27592     5.0  1479545128  2002.0
100415     610    72424     0.5  1493849030  2002.0
100455     610    79501     4.0  1479545378  2002.0

[3642 rows x 5 columns]

## Very quick EDA on the ratings

In [9]:
df_ratings_by_movie = df_ratings[['movieId', 'userId']].groupby("movieId").agg({
    'userId': 'count'
})
df_ratings_by_movie.columns = ['nb_ratings']

In [10]:
df_ratings_by_movie.describe()

nb_ratings
count  9724.000000
mean     10.369807
std      22.401005
min       1.000000
25%       1.000000
50%       3.000000
75%       9.000000
max     329.000000

In [11]:
df_ratings_by_user = df_ratings[['movieId', 'userId']].groupby("userId").agg({
    'movieId': 'count'
})
df_ratings_by_user.columns = ['nb_ratings']
df_ratings_by_user.describe()

nb_ratings
count   610.000000
mean    165.304918
std     269.480584
min      20.000000
25%      35.000000
50%      70.500000
75%     168.000000
max    2698.000000

## Build recommender

In [12]:
reader = Reader()
data = Dataset.load_from_df(df_ratings[['userId', 'movieId', 'rating']], reader)
data_train, data_test = train_test_split(data, test_size=.33)
svd = SVD()
#TODO: add hyperparameter selection
svd.fit(data_train)
predictions = svd.test(data_test)
accuracy.rmse(predictions) #TODO: use other metric to taking ranking into account

RMSE: 0.8836


0.8836116065005458

In [13]:
get_top_k(predictions)

defaultdict(list,
            {348: [(593, 5),
              (4226, 4.94962520884064),
              (858, 4.87756678207728),
              (296, 4.858559235116758),
              (2858, 4.837416466077338),
              (608, 4.630220955585625),
              (79132, 4.602051953330098),
              (8798, 4.538266713849529),
              (2357, 4.48157137465966),
              (3083, 4.431032985009927)],
             539: [(527, 4.259517501055188),
              (6539, 4.095948304163006),
              (1297, 4.095259857280502),
              (4306, 4.0717073845056),
              (3740, 4.030157177707573),
              (68954, 3.976444703650258),
              (31878, 3.9233046335469064),
              (5218, 3.8837762449092206),
              (89864, 3.6928338850372118),
              (3745, 3.609764941398944)],
             142: [(356, 4.4175378504244),
              (593, 4.330529747000501),
              (527, 4.229482878248286),
              (50, 4.1840990710206185),
      

## Evaluate

In [14]:
df_test = pd.read_json(json.dumps(predictions), orient='records')
df_test.columns = ['userId', 'movieId', 'rating', 'predicted_rating', 'log']
df_test = df_test.merge(df_movies[['movieId', 'date']], how='left')

In [15]:
# the segmentation could really be improved #TODO: hyperparameter tuning
fig = go.Figure()
fig.add_trace(go.Violin(
    x=df_test['rating'],
    y=df_test['predicted_rating'],
    name='Distribution of predictions'
))    
fig.add_trace(go.Scatter(
    x=np.arange(0.5, 5.5, 0.5),
    y=np.arange(0.5, 5.5, 0.5),
    name='y=x',
    line=dict(color='grey', width=4, dash='dash') 
))

fig.show()

In [16]:
# Within 2002, the segmentation seems actually slightly better, except for very low ratings (#TODO EDA on low ratings)
fig = go.Figure()
fig.add_trace(go.Violin(
    x=df_test.loc[df_test.date == year_recommendations, 'rating'],
    y=df_test.loc[df_test.date == year_recommendations, 'predicted_rating'],
    name='Distribution of predictions'
))    
fig.add_trace(go.Scatter(
    x=np.arange(0.5, 5.5, 0.5),
    y=np.arange(0.5, 5.5, 0.5),
    name='y=x',
    line=dict(color='grey', width=4, dash='dash') 
))

fig.show()

## Give recommendations

In [17]:
# predicted ratings for an user for the year
userId = 169
k = 3
df_user = df_test[
    (df_test['userId'] == userId)
    & (df_test['date'] == year_recommendations)
].sort_values('rating', ascending=False).reset_index(drop=True)
df_user = df_user.merge(df_movies[['movieId', 'title']], how='left')

In [18]:
fig = px.scatter(df_user, x="rating", y="predicted_rating", hover_data=['title'])
fig.show()

## Interprete

Let's plot the two first dimensions of the latent movie space to interprete the SVD a little bit.

In [19]:
# Access the latent item factors
# https://github.com/NicolasHug/Surprise/issues/119 latent user factors with algo.pu and item factors with algo.qi
svd.pu.shape

(610, 100)

In [37]:
# Map the id the SVD uses with different dimensions for the visualisation (title, date, nb_ratings, genre...)
raw_iid_to_title = partial(get_value_for_key, df=df_movies, col_key='movieId', col_value='title')
raw_iid_to_date = partial(get_value_for_key, df=df_movies, col_key='movieId', col_value='date')
# raw_iid_to_nb_ratings 
def extract_raw_iid(inner_iid, trainset):
    raw_iid = trainset.to_raw_iid(inner_iid)
    return raw_iid
    
func_to_raw = partial(extract_raw_iid, trainset=data_train)

def inner_iid_to_dimension(inner_iid, func_to_raw, func_to_dim):
    raw_iid = func_to_raw(inner_iid)
    value = func_to_dim(raw_iid)
    return value
    
inner_iid_to_title = partial(inner_iid_to_dimension, func_to_raw=func_to_raw, func_to_dim=raw_iid_to_title)
inner_iid_to_date = partial(inner_iid_to_dimension, func_to_raw=func_to_raw, func_to_dim=raw_iid_to_date)

In [44]:
# find titles of movies in the train set
titles_train = np.array(list(map(inner_iid_to_title, data_train.all_items())))
dates_train = np.array(list(map(inner_iid_to_date, data_train.all_items())))

In [46]:
# Plot first two dimensions of the latent movie space
# Good sign: on the first two dimensions, there doesn't seem to be a clear pattern with year
# TODO: color by genre, transparency by n_ratings
fig = go.Figure()
fig.add_trace(go.Scatter(
    x=svd.qi[:, 0],
    y=svd.qi[:, 1],
    mode='markers',
    text=titles_train,
    marker_color=dates_train
))
fig.show()